In [1]:
import pandas as pd

In [2]:
df = pd.read_excel("hoanmy_detect_task.xlsx")

In [3]:
df.head()

Location                                                Job  \
0  Khu vực Ngoại cảnh  Quét lá rụng, thu gom rác lối đi lại, lối xe c...   
1  Khu vực Ngoại cảnh  Nhặt rác bồn hoa cây cảnh, làm sạch gạch ốp xu...   
2  Khu vực Ngoại cảnh                         Vệ sinh gạt tàn, thùng rác   
3  Khu vực Ngoại cảnh  Lau các biển quảng cáo, biển chỉ dẫn (dưới 4m)...   
4  Khu vực Ngoại cảnh   Lau tường đá và kính bên ngoài tòa nhà (dưới 4m)   

  label  Name  luuluong  Dientichngoai  Dientichtrong  
0     1  BIDV         3           1144          11200  
1     1  BIDV         3           1144          11200  
2     1  BIDV         3           1144          11200  
3     1  BIDV         3           1144          11200  
4     2  BIDV         3           1144          11200

In [4]:
import pandas as pd
from pyvi import ViTokenizer


In [5]:
# ==== 1. Load stopword ====

def load_stopwords(path):
    with open(path, "r", encoding="utf-8") as f:
        sw = [line.strip() for line in f if line.strip()]
    return set(sw)

stopwords_path = "vietnamese-stopwords-dash.txt"   # đổi tên nếu khác
vietnamese_stopwords = load_stopwords(stopwords_path)


# ==== 2. Hàm tokenize + bỏ stopword ====

def segment_and_remove_stopwords(text):
    if not isinstance(text, str):
        return ""
    segmented = ViTokenizer.tokenize(text)
    tokens = segmented.split()
    filtered = [tok for tok in tokens if tok not in vietnamese_stopwords]
    return " ".join(filtered)


In [6]:
import pandas as pd
import re
import unicodedata
from pyvi import ViTokenizer

def normalize_text_keep_words(s: str) -> str:
    s = str(s)
    s = unicodedata.normalize('NFC', s).lower()
    s = re.sub(r"[^0-9a-zà-ỹ\s]", " ", s)
    s = re.sub(r"\s+", " ", s).strip()
    return s


def preprocess_pipeline(df_raw: pd.DataFrame) -> pd.DataFrame:
    """
    - Không ghép Location + Job
    - Clean text
    - Word segment Job + remove stopword
    """
    df = df_raw.dropna(subset=["label"]).copy()
    df["label"] = df["label"].astype(str).str.strip()
    df = df[df["label"].isin(["1","2","3","4"])].copy()

    df["Location"] = df["Location"].fillna("Unknown").astype(str)
    df["Job"]      = df["Job"].astype(str)

    # Clean text
    df["location_clean"] = df["Location"].apply(normalize_text_keep_words)
    df["job_clean"]      = df["Job"].apply(normalize_text_keep_words)

    # Word segment + remove stopword
    df["job_segmented"] = df["job_clean"].apply(segment_and_remove_stopwords)

    # Giữ lại các cột numeric nếu có
    keep_cols = [
        "Location","Job","label",
        "location_clean","job_clean","job_segmented"
    ]
    for c in ["Name","luuluong","Dientichngoai","Dientichtrong"]:
        if c in df.columns:
            keep_cols.append(c)

    return df[keep_cols].reset_index(drop=True)


In [7]:
df_out = preprocess_pipeline(df)
df_out.head()


Location                                                Job  \
0  Khu vực Ngoại cảnh  Quét lá rụng, thu gom rác lối đi lại, lối xe c...   
1  Khu vực Ngoại cảnh  Nhặt rác bồn hoa cây cảnh, làm sạch gạch ốp xu...   
2  Khu vực Ngoại cảnh                         Vệ sinh gạt tàn, thùng rác   
3  Khu vực Ngoại cảnh  Lau các biển quảng cáo, biển chỉ dẫn (dưới 4m)...   
4  Khu vực Ngoại cảnh   Lau tường đá và kính bên ngoài tòa nhà (dưới 4m)   

  label      location_clean  \
0     1  khu vực ngoại cảnh   
1     1  khu vực ngoại cảnh   
2     1  khu vực ngoại cảnh   
3     1  khu vực ngoại cảnh   
4     2  khu vực ngoại cảnh   

                                           job_clean  \
0  quét lá rụng thu gom rác lối đi lại lối xe chạ...   
1  nhặt rác bồn hoa cây cảnh làm sạch gạch ốp xun...   
2                          vệ sinh gạt tàn thùng rác   
3  lau các biển quảng cáo biển chỉ dẫn dưới 4m ch...   
4     lau tường đá và kính bên ngoài tòa nhà dưới 4m   

                                       job_segmented  Name  luuluong  \
0  quét lá rụng thu_gom rác lối đi_lại lối xe chạ...  BIDV         3   
1  nhặt rác bồn hoa cây_cảnh sạch gạch ốp xung_qu...  BIDV         3   
2                          vệ_sinh gạt_tàn thùng rác  BIDV         3   
3   lau biển quảng_cáo biển chỉ_dẫn 4m chân cột điện  BIDV         3   
4                           lau tường đá kính tòa 4m  BIDV         3   

   Dientichngoai  Dientichtrong  
0           1144          11200  
1           1144          11200  
2           1144          11200  
3           1144          11200  
4           1144          11200

In [10]:
df_out = df_out[df_out["label"].astype(str).isin(["1", "2", "3"])].reset_index(drop=True)


# ============================================================
# 3. CHIA 3 TẬP: TRAIN / TEST / HOLDOUT
# ============================================================

test_buildings    = ["Keangnam", "CMC"]   # tập test chính
holdout_buildings = ["VIGALCERA"]             # tòa riêng để holdout – sửa theo dữ liệu thực tế

test_df    = df_out[df_out["Name"].isin(test_buildings)].reset_index(drop=True)
holdout_df = df_out[df_out["Name"].isin(holdout_buildings)].reset_index(drop=True)
train_df   = df_out[
    ~df_out["Name"].isin(test_buildings + holdout_buildings)
].reset_index(drop=True)

print("Train:", train_df.shape)
print("Test :", test_df.shape)
print("Holdout:", holdout_df.shape)


Train: (514, 10)
Test : (172, 10)
Holdout: (83, 10)


In [9]:
df_out = df_out[df_out["label"].astype(str).isin(["1", "2", "3"])].reset_index(drop=True)


In [11]:
import pandas as pd
import numpy as np
import re
import unicodedata
from pyvi import ViTokenizer
from transformers import AutoTokenizer, AutoModel
import torch
from sklearn.metrics import classification_report


In [12]:
device = "cuda" if torch.cuda.is_available() else "cpu"
hf_tokenizer = AutoTokenizer.from_pretrained("dangvantuan/vietnamese-embedding")
hf_model = AutoModel.from_pretrained("dangvantuan/vietnamese-embedding").to(device)

def embed_text(text, tokenizer=hf_tokenizer, model=hf_model, device=device):
    encoded = tokenizer(
        text,
        padding=True,
        truncation=True,
        max_length=128,
        return_tensors="pt"
    ).to(device)

    with torch.no_grad():
        output = model(**encoded)

    token_embeddings = output.last_hidden_state   # (1, L, H)
    attention_mask   = encoded["attention_mask"]  # (1, L)

    mask = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    sum_embeds = (token_embeddings * mask).sum(dim=1)  # (1, H)
    lengths   = mask.sum(dim=1)                       # (1,1)
    mean_pooled = sum_embeds / lengths

    return mean_pooled.cpu()  # (1, H)

In [13]:
def cosine_sim(a, b):
    """
    a: (1, H)
    b: (N, H)
    """
    a = a / a.norm(dim=-1, keepdim=True)
    b = b / b.norm(dim=-1, keepdim=True)
    return torch.mm(a, b.t())  # (1, N)


# Embed toàn bộ train job_segmented
train_texts = train_df["job_segmented"].tolist()

train_embeddings = []
for txt in train_texts:
    vec = embed_text(txt)
    train_embeddings.append(vec.squeeze(0))

train_embeddings = torch.stack(train_embeddings)   # (N_train, H)


In [14]:
# 5. HÀM LOCATION SIMILARITY + NUMERIC CLOSENESS
# ============================================================

def location_similarity(q_row, cand_row):
    q_tokens = set(str(q_row["location_clean"]).split())
    c_tokens = set(str(cand_row["location_clean"]).split())
    if not q_tokens or not c_tokens:
        return 0.0
    inter = len(q_tokens & c_tokens)
    union = len(q_tokens | c_tokens)
    return inter / union


def numeric_closeness(q_row, cand_row, alpha_out=0.7, alpha_in=0.7):
    # closeness theo luuluong
    if "luuluong" in q_row and "luuluong" in cand_row:
        if q_row["luuluong"] == cand_row["luuluong"]:
            c_luu = 1.0
        elif abs(q_row["luuluong"] - cand_row["luuluong"]) == 1:
            c_luu = 0.6
        else:
            c_luu = 0.3
    else:
        c_luu = 0.5

    # closeness theo diện tích
    def safe_val(row, col):
        return float(row[col]) if col in row and not pd.isna(row[col]) else 0.0

    q_out = safe_val(q_row, "Dientichngoai")
    q_in  = safe_val(q_row, "Dientichtrong")
    c_out = safe_val(cand_row, "Dientichngoai")
    c_in  = safe_val(cand_row, "Dientichtrong")

    d_out = abs(np.log1p(q_out) - np.log1p(c_out))
    d_in  = abs(np.log1p(q_in)  - np.log1p(c_in))

    c_out = np.exp(-alpha_out * d_out)
    c_in  = np.exp(-alpha_in  * d_in)

    return 0.5 * c_luu + 0.25 * c_out + 0.25 * c_in


In [15]:
def predict_label_for_row(q_row,
                          train_df=train_df,
                          train_embeddings=train_embeddings,
                          tokenizer=hf_tokenizer,
                          model=hf_model,
                          top_k=10,
                          w_numeric=0.4,
                          w_loc=0.6):
    """
    Bước 1: dùng embedding(job_segmented) để chọn top_k ứng viên gần nghĩa nhất.
    Bước 2: trong top_k đó, KHÔNG dùng score text nữa, chỉ dùng:
        - loc_sim   : similarity theo location_clean  [0,1]  (quan trọng nhất)
        - num_c     : numeric_closeness (luuluong + diện tích)  (~0..1.5)
    final_score = w_loc * loc_sim + w_numeric * num_c
    """
    # 1) embed query
    q_vec = embed_text(q_row["job_segmented"], tokenizer, model)  # (1,H)

    # 2) cosine similarity với toàn bộ train → chỉ để CHỌN ỨNG VIÊN
    sims = cosine_sim(q_vec, train_embeddings)[0]  # (N,)

    # 3) lấy top-k job gần nhất theo embedding
    top_k = min(top_k, len(train_df))
    top_scores, top_idx = torch.topk(sims, k=top_k)

    label_scores = {}

    for score, idx in zip(top_scores, top_idx):
        cand_row = train_df.iloc[int(idx)]

        loc_sim = location_similarity(q_row, cand_row)
        num_c   = numeric_closeness(q_row, cand_row)

        final_score = w_loc * loc_sim + w_numeric * num_c

        lbl = str(cand_row["label"])
        label_scores[lbl] = label_scores.get(lbl, 0.0) + final_score

    if not label_scores:
        majority_label = str(train_df["label"].value_counts().idxmax())
        return majority_label, {}

    best_label = max(label_scores, key=label_scores.get)
    return best_label, label_scores


In [23]:
def predict_on_df(df_in: pd.DataFrame,
                  name: str,
                  top_k=5,
                  w_numeric=0.4,
                  w_loc=0.6):
    df = df_in.copy()
    preds = []
    scores = []

    for _, row in df.iterrows():
        pred, sc = predict_label_for_row(
            row,
            train_df=train_df,
            train_embeddings=train_embeddings,
            tokenizer=hf_tokenizer,
            model=hf_model,
            top_k=top_k,
            w_numeric=w_numeric,
            w_loc=w_loc
        )
        preds.append(pred)
        scores.append(sc)

    df["pred_label"]    = preds
    df["score_details"] = scores

    print(f"\n========== KẾT QUẢ TRÊN {name} ==========")
    print(classification_report(
        df["label"].astype(str),
        df["pred_label"].astype(str),
        digits=3
    ))

    return df


In [24]:
test_df_pred    = predict_on_df(test_df, "TEST (Keangnam + CMC)")



========== KẾT QUẢ TRÊN TEST (Keangnam + CMC) ==========
              precision    recall  f1-score   support

           1      0.788     0.848     0.817       105
           2      0.545     0.511     0.527        47
           3      0.667     0.500     0.571        20

    accuracy                          0.715       172
   macro avg      0.667     0.619     0.638       172
weighted avg      0.707     0.715     0.709       172



In [25]:
holdout_df_pred = predict_on_df(holdout_df, "HOLDOUT")



========== KẾT QUẢ TRÊN HOLDOUT ==========
              precision    recall  f1-score   support

           1      0.684     0.907     0.780        43
           2      0.429     0.261     0.324        23
           3      0.667     0.471     0.552        17

    accuracy                          0.639        83
   macro avg      0.593     0.546     0.552        83
weighted avg      0.610     0.639     0.607        83



In [26]:
def get_top_neighbors_for_row(q_row,
                              train_df,
                              train_embeddings,
                              tokenizer,
                              model,
                              top_k=5,
                              w_numeric=0.4,
                              w_loc=0.6):
    """
    Bước 1: dùng embedding(job_segmented) để lấy top_k ứng viên gần nghĩa nhất.
    Bước 2: với mỗi ứng viên, tính:
        - cos_sim       : similarity embedding (chỉ để tham khảo)
        - loc_sim       : similarity theo location_clean
        - num_closeness : theo luuluong + diện tích
        - final_score   : w_loc * loc_sim + w_numeric * num_closeness
    Trả về DataFrame các neighbor, sort theo final_score giảm dần.
    """
    # 1) embed query
    q_vec = embed_text(q_row["job_segmented"], tokenizer, model)  # (1, H)

    # 2) cosine similarity với toàn bộ train
    sims = cosine_sim(q_vec, train_embeddings)[0]  # (N,)

    # 3) lấy top_k index theo sims
    top_k = min(top_k, len(train_df))
    top_scores, top_idx = torch.topk(sims, k=top_k)

    rows = []
    for score, idx in zip(top_scores, top_idx):
        score_val = float(score.item())
        cand = train_df.iloc[int(idx)].copy()

        loc_sim = location_similarity(q_row, cand)
        num_c   = numeric_closeness(q_row, cand)

        final_score = w_loc * loc_sim + w_numeric * num_c

        cand["cos_sim"]       = score_val
        cand["loc_sim"]       = loc_sim
        cand["num_closeness"] = num_c
        cand["final_score"]   = final_score
        rows.append(cand)

    neighbors_df = pd.DataFrame(rows).sort_values("final_score", ascending=False)
    return neighbors_df


In [28]:
# Lọc các case dự đoán sai trên holdout
mis_holdout = holdout_df_pred[
    holdout_df_pred["label"].astype(str) != holdout_df_pred["pred_label"].astype(str)
].copy()

print("Số mẫu sai trên HOLDOUT:", len(mis_holdout))

max_cases = 5   # in tối đa 5 case cho đỡ dài, bạn có thể tăng số này

for i, (_, row) in enumerate(mis_holdout.iterrows(), start=1):
    if i > max_cases:
        break
    if i!=3:
        continue
    print("\n" + "="*100)
    print(f"❌ CASE SAI #{i}")
    print(f"  True label    : {row['label']}")
    print(f"  Pred label    : {row['pred_label']}")
    print(f"  Tòa (Name)    : {row.get('Name', 'N/A')}")
    print(f"  Location      : {row['Location']}")
    print(f"  Lưu lượng     : {row.get('luuluong', 'N/A')}")
    print(f"  DT ngoài      : {row.get('Dientichngoai', 'N/A')}")
    print(f"  DT trong      : {row.get('Dientichtrong', 'N/A')}")
    print("  Job raw       :", row["Job"])
    print("  job_segmented :", row["job_segmented"])
    print("  location_clean:", row["location_clean"])

    # Lấy top neighbors cho case này
    neighbors = get_top_neighbors_for_row(
        row,
        train_df=train_df,
        train_embeddings=train_embeddings,
        tokenizer=hf_tokenizer,
        model=hf_model,
        top_k=5,       # số ứng viên lấy theo embedding
        w_numeric=0.4,
        w_loc=0.6
    )

    print("\n  → Top 10 hàng xóm trong train (sorted theo final_score):")
    cols_show = [
        "label", "Name", "Location",
        "luuluong", "Dientichngoai", "Dientichtrong",
        "Job", "job_segmented",
        "cos_sim", "loc_sim", "num_closeness", "final_score"
    ]
    # Chỉ in cột nào thực sự tồn tại (phòng trường hợp thiếu)
    cols_show = [c for c in cols_show if c in neighbors.columns]

    print(neighbors[cols_show].head(10).to_string(index=False))


Số mẫu sai trên HOLDOUT: 30

❌ CASE SAI #3
  True label    : 3
  Pred label    : 1
  Tòa (Name)    : VIGALCERA
  Location      : Khu vực ngoại cảnh
  Lưu lượng     : 3
  DT ngoài      : 6000
  DT trong      : 4520
  Job raw       : - Làm vệ sinh khu vực đài phun nước
  job_segmented : vệ_sinh khu_vực đài phun
  location_clean: khu vực ngoại cảnh

  → Top 10 hàng xóm trong train (sorted theo final_score):
label         Name                           Location  luuluong  Dientichngoai  Dientichtrong                                                                                                                                Job                                                                         job_segmented  cos_sim  loc_sim  num_closeness  final_score
    1         BIDV                 Khu vực Ngoại cảnh         3           1144          11200                                                                                                          Vệ sinh họng rác (nếu có)           